# Parsing SEC Filing XBRL Document


## Objective

Parse the filing XBRL file to create a DOM like structure that represent the filing data

## References

* [XBRL Specification - Extensible Business Reporting Language (XBRL) 2.1](https://www.xbrl.org/Specification/XBRL-2.1/REC-2003-12-31/XBRL-2.1-REC-2003-12-31+corrected-errata-2013-02-20.html)

* [XBRL US - List of Elements](https://xbrl.us/data-rule/dqc_0015-le/)

**Element Version**|**Element ID**|**Namespace**|**Element Label**|**Element Name**|**Balance Type**|**Definition**
:-----:|:-----:|:-----:|:-----:|:-----:|:-----:|:-----:
1|1367|us-gaap|Interest Expense|InterestExpense|debit|Amount of the cost of borrowed funds accounted for as interest expense.
2|2692|us-gaap|Cash and Cash Equivalents, at Carrying Value|CashAndCashEquivalentsAtCarryingValue|debit|Amount of currency on hand as well as demand deposits with banks or financial institutions. Includes other kinds of accounts that have the general characteristics of demand deposits. Also includes short-term, highly liquid investments that are both readily convertible to known amounts of cash and so near their maturity that they present insignificant risk of changes in value because of changes in interest rates. Excludes cash and cash equivalents within disposal group and discontinued operation.

## XBRL Element

* [Understanding the Financial Report Logical System](https://www.youtube.com/playlist?list=PLqMZRUzQ64B7EWamzDP-WaYbS_W0RL9nt)
* [XBRL - What is us-gaap:OperatingSegmentsMember element anb where is it defined?](https://money.stackexchange.com/questions/148010/xbrl-what-is-us-gaapoperatingsegmentsmember-element-anb-where-is-it-defined)

### Example
For instance, [Qorvo 2020 10K](https://www.sec.gov/Archives/edgar/data/1604778/000160477821000032/rfmd-20210403_htm.xml):

```
<us-gaap:cashandcashequivalentsatcarryingvalue contextref="*" decimals="-3" id="..." unitref="usd">
  1397880000
</us-gaap:cashandcashequivalentsatcarryingvalue>,
<us-gaap:cashandcashequivalentsatcarryingvalue contextref="***" decimals="-3" id="..." unitref="usd">
  714939000
</us-gaap:cashandcashequivalentsatcarryingvalue>,
<us-gaap:cashandcashequivalentsatcarryingvalue contextref="***" decimals="-3" id="..." unitref="usd">
 711035000
</us-gaap:cashandcashequivalentsatcarryingvalue>
```

Corresponds to the Cash and Cash equivalents in the Cash Flow statement.

<img src="../image/edgar_qorvo_2020_10K_CF.png" align="left" width=800 />

---
# Setup

In [418]:
from typing import (
    List,
    Dict
)
import re
import requests
import unicodedata
import bs4
from bs4 import BeautifulSoup
from IPython.core.display import (
    display, 
    HTML
)


In [158]:
%%html
<style>
table {float:left}
</style>

In [159]:
def restore_windows_1252_characters(restore_string):
    """
        Replace C1 control characters in the Unicode string s by the
        characters at the corresponding code points in Windows-1252,
        where possible.
    """

    def to_windows_1252(match):
        try:
            return bytes([ord(match.group(0))]).decode('windows-1252')
        except UnicodeDecodeError:
            # No character at the corresponding code point: remove it.
            return ''
        
    return re.sub(r'[\u0080-\u0099]', to_windows_1252, restore_string)

---
# Load EDGAR Filing XBRL

Download the ```_htm.xml``` file from EDGAR. SEC now requires user-agent header.

In [253]:
# define the url to specific html_text file
CIK = '1604778'
ACCESSION = '000160477821000032'

FILING_DIR_URL = f"https://www.sec.gov/Archives/edgar/data/{CIK}/{ACCESSION}"
XBRL_NAME = "rfmd-20210403_htm.xml"
XBRL_URL = "/".join([FILING_DIR_URL, XBRL_NAME])

XBRL_URL

'https://www.sec.gov/Archives/edgar/data/1604778/000160477821000032/rfmd-20210403_htm.xml'

In [254]:
headers = {"User-Agent": "Company Name myname@company.com"}
response = requests.get(XBRL_URL, headers=headers)

if response.status_code == 200:
    content = response.content.decode("utf-8") 
else:
    print(f"{XBRL_URL} failed with status {response.status_code}")

In [255]:
soup = BeautifulSoup(content, 'html.parser')

## Repoting period

Each 10-K and 10-Q XBRL has the reporting period for the filing. To exclude the other period, e.g. pervious year or quarter, use the ```context id``` for the reporting period.

For instances:

### QRVO 10-K 2020

```
<context id="ifb6ce67cf6954ebf88471dd82daa9247_D20200329-20210403">
    <entity>
    <identifier scheme="http://www.sec.gov/CIK">0001604778</identifier>
    </entity>
    <period>
        <startDate>2020-03-29</startDate>
        <endDate>2021-04-03</endDate>
    </period>
</context>
```

### AMKR 10-K 2020

```
<context id="i5fac0a392353427b8266f185495754d3_D20200101-20201231">
    <entity>
    <identifier scheme="http://www.sec.gov/CIK">0001047127</identifier>
    </entity>
    <period>
        <startDate>2020-01-01</startDate>
        <endDate>2020-12-31</endDate>
    </period>
</context>
```

### AAPL 10-Q 4th QTR 2020

```
<context id="i6e431846933d461fb8c8c0bdf98c9758_D20200927-20201226">
    <entity>
    <identifier scheme="http://www.sec.gov/CIK">0000320193</identifier>
    </entity>
    <period>
        <startDate>2020-09-27</startDate>
        <endDate>2020-12-26</endDate>
    </period>
</context>
```

In [282]:
CONTEXT = None
for context in soup.find_all('context'):
    if context.find('period') and context.find('period').find('enddate'):
        CONTEXT = context
        break        
        
assert CONTEXT is not None, "Report period not found"

cik_value_in_statement = int(CONTEXT.find('identifier').text.strip())
assert int(CIK) == cik_value_in_statement, \
    "The CIK %s in statement does not match %s" % (cik_value_in_statement, int(CIK))

CONTEXT_ID = CONTEXT['id']
PERIOD = CONTEXT.find('period').find('enddate').text.strip()

print(f"PERIOD is {PERIOD}. CONTEXT_ID is {CONTEXT_ID}")

PERIOD is 2021-04-03. CONTEXT_ID is ifb6ce67cf6954ebf88471dd82daa9247_D20200329-20210403


### Regexp to find all the contexts that match with PERIOD

In [315]:
contexts_regexp = "|".join([
    context['id']
    for context in soup.find_all('context') 
    if context.find('period') and context.find('period').find(['instant'], string=PERIOD)
])
contexts_regexp = rf"{CONTEXT_ID}|" + contexts_regexp
CONTEXT_REGEXP = re.compile(contexts_regexp)

re.compile(r'ifb6ce67cf6954ebf88471dd82daa9247_D20200329-20210403|i531402faf1d04969ac2b2ba0e1680766_I20210403|i614b3f0255fa4fe498adaa07f0fbf60d_I20210403|if0ab0ef720414683923a7f402785ad3e_I20210403|icb4dc0de822e45e083def95ba18db63b_I20210403|i0f82412676864465bc95153e8c1b49ab_I20210403|ib337c97f64d049a98de2e11e47ebd53c_I20210403|ic35c9f161624472cab00e3f84caf65d3_I20210403|i8f2867e16ff34d84980fb01f7fdc0deb_I20210403|i584f22879eac401999cad359b970f36b_I20210403|ie3182c8d89a24851868143b44e560e86_I20210403|if65b2d0205ae464899ea2e3bf8489367_I20210403|i29e1b8251d804774901c92c083244d7a_I20210403|i6f106df87edd413fb3a8a048107b0ad6_I20210403|i4c6964fbdb084ad59dea9a92f4d093e1_I20210403|i5db07e9690b7468c88e7a541bac337b9_I20210403|i3b2c0a00108a41118888df132912220e_I20210403|i7c99ac3cffe2412c849a29735697e90e_I20210403|i89fe86bfae744b4fa8bbaa0ae035a2b3_I20210403|i240b3c84eb8c4038ace3630819e90011_I20210403|i1e062f32c078450f827f3db92bd84514_I20210403|i091de22f4ca94679b13356db21c7167f_I20210403|i1c75a03c4

In [312]:
# regexp to extract numeric string
REGEXP_NUMERIC = re.compile(r"\s*[\d.-]*\s*")

re.match(REGEXP_NUMERIC, " -123.12 ")

<re.Match object; span=(0, 9), match=' -123.12 '>

# Constant

In [321]:
NAMESPACE = "us-gaap"

# Utilities

In [392]:
def find_financial_elements(soup, element_names):
    """Find the financial statement elements from the XML/HTML source.
    Args:
        soup: BS4 source
        element_names: Single string or regexp instance to match the financial elements.
    """
    assert isinstance(soup, BeautifulSoup)
    assert isinstance(element_names, re.Pattern) or isinstance(element_names, str)

    names = element_names.lower() if isinstance(element_names, str) else element_names
    return soup.findAll(
        name=names,
        string=REGEXP_NUMERIC,
        attrs={
            "contextref": CONTEXT_REGEXP,
            "decimals": True, 
            "unitref": True
        }
)

In [422]:
def get_financial_element_numeric_values(elements):
    assert isinstance(elements, bs4.element.ResultSet)
    
    values = []
    for element in elements:
        assert re.match(REGEXP_NUMERIC, element.text.strip()), f"Element must be numeric but {element.text}"
        values.append(float(element.text))
        
    return values

In [423]:
def display_items(elements):
    assert isinstance(elements, bs4.element.ResultSet)
    for element in elements: # decimals="-3" means the displayed value is divied by 1000.
        print(f"{element.name} {element['unitref']:5} {element['decimals']:5} {element.text:15} ")

---
# Statements of Income (P/L)

## Revenues

In [394]:
revenues = find_financial_elements(soup=soup, element_names=re.compile(rf"{NAMESPACE}:Revenues".lower()))
display_items(revenues)

us-gaap:revenues usd   -3    4015307000      
us-gaap:revenues usd   -3    4015307000      


## Cost of Revenues

In [401]:
names = re.compile("|".join([
    rf"{NAMESPACE}:CostOfRevenue",
    rf"{NAMESPACE}:CostOfGoods",
    rf"{NAMESPACE}:CostOfGoodsAndServicesSold",
]).lower())

costs_of_revenues = find_financial_elements(soup=soup, element_names=names)
display_items(costs_of_revenues)

us-gaap:costofgoodsandservicessold usd   -3    2131741000      


## Operating Expenses

In [424]:
names = f"{NAMESPACE}:OperatingExpenses".lower()

operating_expense_total = find_financial_elements(soup=soup, element_names=names)
display_items(operating_expense_total) 

us-gaap:operatingexpenses usd   -3    976939000       
976939000.0


### Research and Development

In [412]:
names = f"{NAMESPACE}:ResearchAndDevelopmentExpense".lower()

operating_expense_r_and_d = find_financial_elements(soup=soup, element_names=names)
display_items(operating_expense_r_and_d) 

us-gaap:researchanddevelopmentexpense usd   -3    570395000       


### Administrative Expense

In [413]:
names = f"{NAMESPACE}:SellingGeneralAndAdministrativeExpense"

operating_expense_administrative = find_financial_elements(soup=soup, element_names=names)
display_items(operating_expense_administrative) 

us-gaap:sellinggeneralandadministrativeexpense usd   -3    367238000       


### Other expenses

In [414]:
names = f"{NAMESPACE}:OtherCostAndExpenseOperating"

operating_expense_other = find_financial_elements(soup=soup, element_names=names)
display_items(operating_expense_other) 

us-gaap:othercostandexpenseoperating usd   -3    39306000        


## Gross Profit

In [415]:
names = f"{NAMESPACE}:GrossProfit"

gross_profit = find_financial_elements(soup=soup, element_names=names)
display_items(gross_profit) 

us-gaap:grossprofit usd   -3    1883566000      


---
# Balance Sheet (B/S)

## Cash & Cash Equivalents

Look for the cash and cash equivalents for the reporting perid in the Balance Sheet and Cash Flow statements of the  10-K.

In [404]:
names = f"{NAMESPACE}:CashAndCashEquivalentsAtCarryingValue"

cash_equivalents = find_financial_elements(soup=soup, element_names=names)
display_items(cash_equivalents) 

us-gaap:cashandcashequivalentsatcarryingvalue usd   -3    1397880000      
us-gaap:cashandcashequivalentsatcarryingvalue usd   -3    1397880000      


---

## Shares Outstanding

In [410]:
names = re.compile("|".join([
    rf"{NAMESPACE}:SharesOutstanding",
    rf"{NAMESPACE}:CommonStockSharesOutstanding",
    rf"{NAMESPACE}:CommonStockOtherSharesOutstanding",
]).lower())

shares_outstanding = find_financial_elements(soup=soup, element_names=names)
display_items(shares_outstanding)

us-gaap:commonstocksharesoutstanding shares -3    112557000       
us-gaap:commonstocksharesoutstanding shares -3    112557000       


## HTML

In [218]:
html = soup.find(
    name=re.compile(r"us-gaap:organizationconsolidationandpresentationoffinancialstatementsdisclosuretextblock"),
    attrs={
        "contextref": CONTEXT_ID
    }
).text


In [219]:
# NOTE: HTML needs "str" for the data argument, cannot accept bs4.element.Tag
HTML(data=str(html))

---

# Loading Edgar XBRL in HTML

Download the ```.htm``` file from EDGAR.

In [220]:
XBRL_HTML_NAME = "rfmd-20210403.htm"
XBRL_HTML_URL = "/".join([FILING_DIR_URL, XBRL_HTML_NAME])

XBRL_HTML_URL

'https://www.sec.gov/Archives/edgar/data/1604778/000160477821000032/rfmd-20210403.htm'

In [221]:
headers = {"User-Agent": "Company Name myname@company.com"}
response = requests.get(XBRL_HTML_URL, headers=headers)

if response.status_code == 200:
    content = response.content.decode("utf-8") 
else:
    print(f"{XBRL_HTML_URL} failed with status {response.status_code}")

In [246]:
soup = BeautifulSoup(content, 'html.parser')
# soup

<?xml version="1.0" ?><!--XBRL Document Created with Wdesk from Workiva--><!--Copyright 2021 Workiva--><!--r:91aade29-fc9e-43a6-bad1-aa48cbf2501b,g:1a9d9b7b-acb7-4f7a-9f0b-8f954fcc97d8,d:1283705588d7426681f1567ea616af0a--><html xml:lang="en-US" xmlns="http://www.w3.org/1999/xhtml" xmlns:country="http://xbrl.sec.gov/country/2020-01-31" xmlns:dei="http://xbrl.sec.gov/dei/2020-01-31" xmlns:iso4217="http://www.xbrl.org/2003/iso4217" xmlns:ix="http://www.xbrl.org/2013/inlineXBRL" xmlns:ixt="http://www.xbrl.org/inlineXBRL/transformation/2015-02-26" xmlns:ixt-sec="http://www.sec.gov/inlineXBRL/transformation/2015-08-31" xmlns:link="http://www.xbrl.org/2003/linkbase" xmlns:rfmd="http://www.rfmd.com/20210403" xmlns:srt="http://fasb.org/srt/2020-01-31" xmlns:us-gaap="http://fasb.org/us-gaap/2020-01-31" xmlns:xbrldi="http://xbrl.org/2006/xbrldi" xmlns:xbrli="http://www.xbrl.org/2003/instance" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance"><head><m

In [245]:
# NOTE: In HTML, "name" is a tag attribute, NOT the tag name.
gaap_elements = soup.findAll(
    string=re.compile(r"[ 0-9.,]"),
    attrs={
        "name" : re.compile("us-gaap:.*"), 
        "contextref": re.compile(contexts_regexp),
        "decimals": True, 
        "unitref": True
    }
)

for element in gaap_elements: # Scale="3" means the value is per 1000.
    # print(element.prettify(formatter="html"))
    print(f"{element['name']:60} {element.text:15} {element['unitref']:12} {element['decimals']:5}")

us-gaap:AllowanceForDoubtfulAccountsReceivableCurrent        331             usd          -3   
us-gaap:PreferredStockParOrStatedValuePerShare               0.0001          usdPerShare  INF  
us-gaap:PreferredStockSharesAuthorized                       5,000           shares       -3   
us-gaap:CommonStockParOrStatedValuePerShare                  0.0001          usdPerShare  4    
us-gaap:CommonStockSharesAuthorized                          405,000         shares       -3   
us-gaap:CommonStockSharesIssued                              112,557         shares       -3   
us-gaap:CommonStockSharesOutstanding                         112,557         shares       -3   
us-gaap:CashAndCashEquivalentsAtCarryingValue                1,397,880       usd          -3   
us-gaap:AccountsReceivableNetCurrent                         457,431         usd          -3   
us-gaap:InventoryNet                                         507,787         usd          -3   
us-gaap:PrepaidExpenseCurrent           

In [249]:
re.match(r"-[\d]*", "-123")

<re.Match object; span=(0, 4), match='-123'>

## Extract pages from the XBRL in HTML

In [106]:
def split_document_html_into_pages(html: str):
    """
    Extract each page in the HTML tag using the HR tag string as the page break.
    HTML in DOCUMENT is sectioned into pages with the HR tag, e.g. 
    <hr align="CENTER" size="3" style="COLOR:#999999" width="100%"/>. 
    
    Args:
        HTML in string format, not BS4 tag object.
    """
    assert isinstance(html, str), f"Invalid arg of type {type(html)}"
    
    page_breaks_regexp = "|".join([
        re.escape(str(page_break)) 
        for page_break in BeautifulSoup(html, 'html.parser').find_all('hr', {'width':'100%'})
    ])
    pages = re.split(page_breaks_regexp, str(html))
    return pages

In [116]:
# NOTE: HTML needs "str" for the data argument, cannot accept bs4.element.Tag
HTML(data=str(soup.find('html').extract()))